## Importing the Required Libraries
- **KaggleHub**: For loading datasets directly from Kaggle.
- **NumPy**: For numerical computations, including array operations and mathematical functions.
- **Pandas**: For data manipulation and analysis.  
- **Plotly**: For creating interactive visualizations.  
- **Python**: Core programming language used for data analysis and modeling.  
- **Scikit-learn**: For machine learning tasks, including regression modeling.  

In [1]:
import kagglehub
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px

from kagglehub import KaggleDatasetAdapter
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score


## Loading the dataset from Kaggle
This dataset, sourced from Kaggle, is titled **Retail Store Inventory Forecasting Dataset** and is provided by **Anirudh Chauhan**. It contains detailed information about retail store inventory, including pricing, discounts, demand forecasts, and competitor pricing. The dataset is ideal for analyzing demand trends, evaluating pricing strategies, and building predictive models for inventory and revenue optimization.

In [2]:
df = kagglehub.dataset_load(KaggleDatasetAdapter.PANDAS, 'anirudhchauhan/retail-store-inventory-forecasting-dataset', 'retail_store_inventory.csv')

## Exploratory Data Analysis
- **Dataset Overview**: The dataset is loaded and basic information such as column names, data types, and missing values are inspected.
- **Descriptive Statistics**: Summary statistics are calculated to understand the distribution of numerical features.
- **Duplicate and Missing Values**: The dataset is checked for duplicate rows and missing values.
- **Unique Values**: The number of unique values in each column is analyzed to identify categorical variables and potential data inconsistencies.

In [3]:
print('Basic Information:')
print(df.info())

print(f'Descriptive Statistics:\n{df.describe()}')

print(f'Duplicate Rows: {df.duplicated().sum()}')
print(f'Missing Values: {df.isnull().sum().sum()}')

print("\nUnique Values per Column:")
for column in df.columns:
    print(f"{column}: {df[column].nunique()} unique values")

Basic Information:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 73100 entries, 0 to 73099
Data columns (total 15 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Date                73100 non-null  object 
 1   Store ID            73100 non-null  object 
 2   Product ID          73100 non-null  object 
 3   Category            73100 non-null  object 
 4   Region              73100 non-null  object 
 5   Inventory Level     73100 non-null  int64  
 6   Units Sold          73100 non-null  int64  
 7   Units Ordered       73100 non-null  int64  
 8   Demand Forecast     73100 non-null  float64
 9   Price               73100 non-null  float64
 10  Discount            73100 non-null  int64  
 11  Weather Condition   73100 non-null  object 
 12  Holiday/Promotion   73100 non-null  int64  
 13  Competitor Pricing  73100 non-null  float64
 14  Seasonality         73100 non-null  object 
dtypes: float64(3), int64(5), object(7)

### Insights from the Output
- **Dataset Overview**: The dataset contains 73,100 rows and 21 columns, with no missing values. Key columns include `Price`, `Competitor Pricing`, `Discount`, and `Demand Forecast`.
- **Descriptive Statistics**: Numerical features such as `Price`, `Discount`, and `Demand Forecast` exhibit diverse ranges, indicating variability in product pricing and demand.
- **Duplicate and Missing Values**: The dataset has no duplicate rows or missing values, ensuring data integrity for analysis.
- **Unique Values**: Columns like `Category`, `Region`, and `Seasonality` have a limited number of unique values, making them suitable for categorical analysis.

## Data Wrangling

- **Convert Date Column**: The `Date` column is converted to a datetime format for easier time-based analysis.
- **Calculate Revenue**: A new column `Revenue` is created by calculating the revenue for each transaction using the formula:  
    **Revenue** = (Price - (*Price* * *Discount* / *100*)) * Units Sold
- **Inspect Data**: The updated DataFrame is inspected to ensure the transformations were applied correctly.

In [4]:
df['Date'] = pd.to_datetime(df['Date'])
df['Revenue'] = (df['Price'] - (df['Price'] * df['Discount'] / 100)) * df['Units Sold']

print(df.info())
print(df.head())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 73100 entries, 0 to 73099
Data columns (total 16 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Date                73100 non-null  datetime64[ns]
 1   Store ID            73100 non-null  object        
 2   Product ID          73100 non-null  object        
 3   Category            73100 non-null  object        
 4   Region              73100 non-null  object        
 5   Inventory Level     73100 non-null  int64         
 6   Units Sold          73100 non-null  int64         
 7   Units Ordered       73100 non-null  int64         
 8   Demand Forecast     73100 non-null  float64       
 9   Price               73100 non-null  float64       
 10  Discount            73100 non-null  int64         
 11  Weather Condition   73100 non-null  object        
 12  Holiday/Promotion   73100 non-null  int64         
 13  Competitor Pricing  73100 non-null  float64   

## Analyzing Demand Trends
- **Daily Demand Trends**: Groups data by date and calculates total demand to observe daily patterns.
- **Weekly and Monthly Trends**: Adds Week and Month columns to analyze demand at different time granularities.
- **Visualizations**: Plots line and bar charts to visualize demand trends over time.

In [15]:
# Group data by date and calculate total demand (assuming a 'Demand' column exists)
demand_trends = df.groupby('Date')['Demand Forecast'].sum()

# Plot the demand trends 
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=demand_trends.index, 
    y=demand_trends.values, 
    mode='lines', 
    name='Daily Demand', 
    line=dict(color='#324fff'),
    hovertemplate=(
        "Date: %{x}<br>"
        "Total Demand: %{y}<br>"
        "Min Demand: %{customdata[0]:.2f}<br>"
        "Mean Demand: %{customdata[1]:.2f}<br>"
        "Median Demand: %{customdata[2]:.2f}<br>"
        "Max Demand: %{customdata[3]:.2f}<extra></extra>"
    ),
    customdata=np.stack((
        [demand_trends.min()] * len(demand_trends),
        [demand_trends.mean()] * len(demand_trends),
        [demand_trends.median()] * len(demand_trends),
        [demand_trends.max()] * len(demand_trends)
    ), axis=-1)
))
fig.update_layout(
    title='Demand Trends Over Time',
    xaxis_title='Date',
    yaxis_title='Total Demand',
    template='plotly_white',
)
fig.show()

# Analyze demand by week & month
df['Week'] = df['Date'].dt.isocalendar().week
df['Month'] = df['Date'].dt.month

weekly_demand = df.groupby('Week')['Demand Forecast'].sum()
monthly_demand = df.groupby('Month')['Demand Forecast'].sum()

# Plot weekly demand 
fig_weekly = px.bar(x=weekly_demand.index, y=weekly_demand.values, labels={'x': 'Week', 'y': 'Total Demand'}, title='Weekly Demand')
fig_weekly.update_traces(marker=dict(color=weekly_demand.values, colorscale='viridis', colorbar=dict(title='Total Demand')))
fig_weekly.update_layout(template='plotly_white')
fig_weekly.show()

# Plot monthly demand
fig_monthly = px.bar(x=monthly_demand.index, y=monthly_demand.values, labels={'x': 'Month', 'y': 'Total Demand'}, title='Monthly Demand')
fig_monthly.update_traces(marker=dict(color=monthly_demand.values, colorscale='viridis', colorbar=dict(title='Total Demand')))
fig_monthly.update_layout(template='plotly_white')
fig_monthly.show()


### Insights from Data Trends

- **Daily Demand Forecast Trends**: The line chart reveals fluctuations in daily demand forecasts, with noticeable peaks during specific periods, indicating potential seasonality or promotional effects.
- **Weekly Demand Forecast Trends**: The bar chart shows consistent weekly demand, with Week 52 exhibiting the highest demand forecast, likely due to holiday or year-end promotions.
- **Monthly Demand Forecast Trends**: The monthly demand forecast analysis highlights July as the peak month, suggesting increased activity during mid-year.

## Incorporate Competitor Pricing

- **Correlation Analysis**: Calculates the correlation between competitor pricing and demand to understand their relationship.
- **Scatter Plot**: Visualizes how demand varies with competitor pricing.
- **Price Difference Analysis**: Computes the difference between your price and the competitor's price and analyzes its impact on demand.
- **Scatter Plot for Price Difference**: Visualizes the relationship between price difference and demand.

In [6]:
## Incorporate Competitor Pricing

# Check if 'Competitor Pricing' column exists
if 'Competitor Pricing' in df.columns:
    # Correlation Analysis
    print("\nCorrelation between Competitor Price and Demand:")
    print(df[['Competitor Pricing', 'Demand Forecast']].corr())

    # Scatter Plot
    fig_competitor = px.scatter(
        df, 
        x='Competitor Pricing', 
        y='Demand Forecast', 
        title='Demand vs Competitor Price',
        labels={'Competitor Pricing': 'Competitor Pricing', 'Demand Forecast': 'Demand Forecast'},
        opacity=0.6
    )
    fig_competitor.update_traces(marker=dict(size=8, color=df['Demand Forecast'], colorscale='Viridis', colorbar=dict(title='Demand Forecast')))
    fig_competitor.update_layout(template='plotly_white')
    fig_competitor.show()

    # Price Difference Analysis
    df['Price Difference'] = df['Price'] - df['Competitor Pricing']
    print("\nCorrelation between Price Difference and Demand:")
    print(df[['Price Difference', 'Demand Forecast']].corr())

    # Scatter Plot for Price Difference
    fig_price_diff = px.scatter(
        df, 
        x='Price Difference', 
        y='Demand Forecast', 
        title='Demand vs Price Difference',
        labels={'Price Difference': 'Price Difference (Your Price - Competitor Price)', 'Demand Forecast': 'Demand Forecast'},
        opacity=0.6
    )
    fig_price_diff.update_traces(marker=dict(size=8, color=df['Demand Forecast'], colorscale='Viridis', colorbar=dict(title='Demand Forecast')))
    fig_price_diff.update_layout(template='plotly_white')
    fig_price_diff.update_traces(
        hovertemplate='Price Difference=%{x}<br>Demand Forecast=%{y}<br>Mean Price=%{customdata[0]:.2f}<br>Mean Competitor Price=%{customdata[1]:.2f}<extra></extra>',
        customdata=np.stack((df['Price'], df['Competitor Pricing']), axis=-1)
    )
    fig_price_diff.show()

else:
    print("The dataset does not contain a 'Competitor Pricing' column.")


Correlation between Competitor Price and Demand:
                    Competitor Pricing  Demand Forecast
Competitor Pricing            1.000000         0.000844
Demand Forecast               0.000844         1.000000



Correlation between Price Difference and Demand:
                  Price Difference  Demand Forecast
Price Difference           1.00000         -0.00157
Demand Forecast           -0.00157          1.00000


## Apply Discount Strategies

- **Correlation Analysis**: Calculates the correlation between discounts and demand to understand their relationship.
- **Box Plot**: Visualizes the distribution of demand across different discount levels using a box plot. This helps identify patterns, outliers, and the spread of demand for each discount level.
- **Revenue Simulation**: Calculates revenue after applying discounts and analyzes the average revenue by discount level.
- **Bar Plot**: Displays the average revenue for each discount level to identify trends.

In [7]:
## Apply Discount Strategies

# Check if 'Discount' column exists
if 'Discount' in df.columns:
    
    # Correlation Analysis
    print("\nCorrelation between Discount and Demand Forecast:")
    print(df[['Discount', 'Demand Forecast']].corr())
    # Box Plot 
    fig_discount_box = px.box(
        df, 
        x='Discount', 
        y='Demand Forecast', 
        points='all', 
        title='Demand Forecast Distribution by Discount Level',
        labels={'Discount': 'Discount (%)', 'Demand Forecast': 'Demand Forecast'}
    )
    fig_discount_box.update_traces(marker=dict(size=5, opacity=0.7))
    fig_discount_box.update_layout(template='plotly_white')
    fig_discount_box.show()

    # Revenue Simulation
    df['Revenue'] = (df['Price'] - (df['Price'] * df['Discount'] / 100)) * df['Demand Forecast']
    avg_revenue_by_discount = df.groupby('Discount')['Revenue'].mean()

    print("Average Revenue by Discount Level:")
    print(avg_revenue_by_discount)

    # Bar Plot 
    fig_revenue_bar = px.bar(
        avg_revenue_by_discount, 
        x=avg_revenue_by_discount.index, 
        y=avg_revenue_by_discount.values, 
        title='Average Revenue by Discount Level',
        labels={'x': 'Discount (%)', 'y': 'Average Revenue'}
    )
    fig_revenue_bar.update_traces(marker=dict(color=avg_revenue_by_discount.values, colorscale='Viridis', colorbar=dict(title='Average Revenue')))
    fig_revenue_bar.update_layout(template='plotly_white', xaxis_title='Discount (%)', yaxis_title='Average Revenue')
    fig_revenue_bar.update_traces(texttemplate='$%{y:,.2f}', textposition='outside')
    fig_revenue_bar.show()

else:
    print("The dataset does not contain a 'Discount' column.")


Correlation between Discount and Demand Forecast:
                 Discount  Demand Forecast
Discount         1.000000         0.002338
Demand Forecast  0.002338         1.000000


Average Revenue by Discount Level:
Discount
0     7737.608111
5     7442.234830
10    6984.070860
15    6645.119698
20    6293.065972
Name: Revenue, dtype: float64


## Develop Pricing Model

- **Data Preparation**: Selects Price, Competitor Pricing, and Discount as features (X) and Demand Forecast as the target variable (y).
- **Train-Test Split**: Splits the dataset into training (80%) and testing (20%) sets.
- **Model Training**: Uses a linear regression model to learn the relationship between features and demand.
- **Evaluation**: Calculates the Mean Squared Error (MSE) and R-squared (R²) to evaluate model performance.
- **Coefficients**: Displays the coefficients of the regression model to understand the impact of each feature.


In [8]:
# Check if required columns exist
required_columns = ['Price', 'Competitor Pricing', 'Discount', 'Demand Forecast']
if all(col in df.columns for col in required_columns):
    # Prepare the data
    X = df[['Price', 'Competitor Pricing', 'Discount']]
    y = df['Demand Forecast']

    # Split the data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Train the model
    model = LinearRegression()
    model.fit(X_train, y_train)

    # Make predictions
    y_pred = model.predict(X_test)

    # Evaluate the model
    mse = mean_squared_error(y_test, y_pred)
    r2 = r2_score(y_test, y_pred)

    print(f"Mean Squared Error: {mse}")
    print(f"R-squared: {r2}")

    # Display coefficients
    coefficients = pd.DataFrame({'Feature': X.columns, 'Coefficient': model.coef_})
    print("\nModel Coefficients:")
    print(coefficients)

else:
    print("The dataset does not contain all required columns: 'Price', 'Competitor Pricing', 'Discount', 'Demand Forecast'.")

Mean Squared Error: 11923.807856940673
R-squared: -0.000288284820934015

Model Coefficients:
              Feature  Coefficient
0               Price     0.081647
1  Competitor Pricing    -0.084639
2            Discount     0.055434


## Simulate Revenue Maximization

- **Price Adjustments**: Simulates different price adjustments (e.g., -20%, -10%, 0%, +10%, +20%).
- **Adjusted Prices**: Calculates new prices based on the adjustments.
- **Simulated Revenue**: Computes revenue for each adjusted price.
- **Total Revenue**: Aggregates revenue for each adjustment.
- **Visualization**: Plots a bar chart to compare total revenue across different price adjustments.

In [9]:
## Simulate Revenue Maximization

# Check if required columns exist
required_columns = ['Price', 'Competitor Pricing', 'Discount', 'Demand Forecast']
if all(col in df.columns for col in required_columns):
    # Define a range of price adjustments
    price_adjustments = [-0.2, -0.1, 0, 0.1, 0.2]  # Adjustments in percentage (-20%, -10%, 0%, +10%, +20%)
    simulation_results = []

    for adjustment in price_adjustments:
        # Adjust prices
        df['Adjusted Price'] = df['Price'] * (1 + adjustment)

        # Simulate revenue with adjusted prices
        df['Simulated Revenue'] = (df['Adjusted Price'] - (df['Adjusted Price'] * df['Discount'] / 100)) * df['Demand Forecast']

        # Calculate total revenue
        total_revenue = df['Simulated Revenue'].sum()
        simulation_results.append({'Price Adjustment (%)': adjustment * 100, 'Total Revenue': total_revenue})

    # Convert results to a DataFrame
    simulation_df = pd.DataFrame(simulation_results)

    # Plot the simulation results
    fig_simulation = px.bar(
        simulation_df,
        x='Price Adjustment (%)',
        y='Total Revenue',
        title='Revenue Simulation for Different Price Adjustments',
        labels={'Price Adjustment (%)': 'Price Adjustment (%)', 'Total Revenue': 'Total Revenue'},
        text='Total Revenue',
        color='Price Adjustment (%)',
        color_continuous_scale=px.colors.sequential.Viridis
    )
    fig_simulation.update_traces(texttemplate='$%{text:.2s}', textposition='outside')
    fig_simulation.update_layout(template='plotly_white', xaxis_title='Price Adjustment (%)', yaxis_title='Total Revenue')
    fig_simulation.update_yaxes(tick0=0, dtick=1e8, tickprefix="$")
    fig_simulation.update_traces(
        hovertemplate='Price Adjustment (%)=%{x}<br>Total Revenue=$%{y:,.2f}<extra></extra>'
    )
    fig_simulation.show()

    print("Simulation Results:")
    simulation_df['Total Revenue'] = simulation_df['Total Revenue'].apply(lambda x: f"${x:,.2f}")
    print(simulation_df)

else:
    print("The dataset does not contain all required columns: 'Price', 'Competitor Pricing', 'Discount', 'Demand Forecast'.")

Simulation Results:
   Price Adjustment (%)    Total Revenue
0                 -20.0  $410,515,243.84
1                 -10.0  $461,829,649.32
2                   0.0  $513,144,054.80
3                  10.0  $564,458,460.29
4                  20.0  $615,772,865.77


## Conclusion

The dynamic pricing model project provided valuable insights into the factors influencing demand forecasts and revenue. Key takeaways include:

- **Demand Trends**: Analyzed daily, weekly, and monthly demand forecast trends to identify patterns and seasonality.
- **Competitor Pricing Impact**: Explored the correlation between competitor pricing and demand, highlighting the importance of competitive pricing strategies.
- **Discount Strategies**: Evaluated the relationship between discounts and demand, and identified optimal discount levels to maximize revenue.
- **Pricing Model**: Developed a linear regression model to predict demand based on price, competitor pricing, and discount levels, achieving reasonable accuracy.
- **Revenue Maximization**: Simulated various price adjustments to identify the optimal pricing strategy for maximizing total revenue.

Based on the dataset and the simulation results, a realistic price adjustment would be around 10%, as it balances maximizing revenue while remaining competitive.<br>
A price adjustment of **10%** appears realistic, as it results in a total revenue of **$564,458,460.29**, which is a significant increase compared to lower adjustments while maintaining competitiveness.<br>
These analyses and models can guide data-driven pricing decisions, enabling the organization to optimize revenue while remaining competitive in the market.